## 1. Import libraries

In [1]:
import sys
sys.path.append('../')

%matplotlib inline
from collections import defaultdict
from typing import List
from sklearn.preprocessing import StandardScaler

import numpy as np
import time
import matplotlib.pyplot as plt
import seaborn as sns

import gym

import src.agents as agents
import src.episode as episode
import src.environment as environment
import src.aux_plots as aux_plots

## 2. Auxiliary functions

### 2.1. Reduce state space

In [2]:
def reduce_state(ob):
    # Doesn't matter where we were hit
    ob[16] = 1 if ob[16] != 255 else 0

    # Reduce chicken y-position
    ob[14] = ob[14] // 3

    for b in range(108, 118):
        # The chicken is in the x-posistion ~49
        if ob[b] < 20 or ob[b] > 80:
            # We don't need to represent cars far from the chicken
            ob[b] = 0
        else:
            # Reduce the cars x-positions sample space
            ob[b] = ob[b] // 3

    return ob

### 2.2. Reward policy

In [3]:
def reward_policy(reward, ob, action):
    if reward == 1:
        reward = reward_policy.REWARD_IF_CROSS
    elif ob[16] == 1:  # Collision!
        reward = reward_policy.REWARD_IF_COLISION
    elif action != 1:  # Don't incentivate staying still
        reward = reward_policy.REWARD_IF_STILL

    return reward

### 2.3. Print results

In [4]:
def print_result(i, scores, total_reward, score):
#     if i % 10 == 0:
        print(f"Run [{i:4}] - Total reward: {total_reward:7.2f} Mean scores: {sum(scores) / len(scores):.2f} Means Scores[:-10]: {sum(scores[-10:]) / len(scores[-10:]):5.2f} Score: {score:2} ")

## 3. Running algorithms

### 3.1. Hyperparameters

In [5]:
RAM_mask = [
      14  # Chicken Y
    , 16  # Chicken Lane Collide
    , 108, 109, 110, 111, 112, 113, 114, 115, 116, 117  # Car X Coords
]

GAMMA = 0.99
AVAILABLE_ACTIONS = 2
N0 = 2.5

reward_policy.REWARD_IF_CROSS = 50
reward_policy.REWARD_IF_COLISION = -1
reward_policy.REWARD_IF_STILL = -0.1

### 3.2. Monte Carlo

In [ ]:
env, initial_state = environment.get_env()

mc_agent = agents.MonteCarloControl(gamma=GAMMA, available_actions=AVAILABLE_ACTIONS, N0=N0)

In [ ]:
def MonteCarloES(agent, reduce_s, reward_p, RAM_mask: List[int], render: bool=False):
    epi = episode.generate_episode(env, reduce_state=reduce_s, reward_policy=reward_p, agent=agent, RAM_mask=RAM_mask, render=render)
    return agent.update_policy(epi)

In [ ]:
# %%time
# MonteCarloES(agent=mc_agent,reduce_s=reduce_state, reward_p=reward_policy, RAM_mask=RAM_mask, render=False)

In [ ]:
%%time
scores = []
total_rewards = []


n_runs = 5

for i in range(n_runs):
    render = i % 201 == 200

    score, total_reward = MonteCarloES(agent=mc_agent,reduce_s=reduce_state, reward_p=reward_policy, RAM_mask=RAM_mask, render=render)

    scores.append(score)
    total_rewards.append(total_reward)

    print_result(i, scores, total_reward, score)

### 3.3. Q Learning

In [ ]:
env, initial_state = environment.get_env()
ql_agent = agents.QLearning(gamma=GAMMA, available_actions=AVAILABLE_ACTIONS, N0=N0)

In [ ]:
%%time
scores = []
total_rewards = []

n_runs = 1
render = False
for i in range(n_runs):
#     render = i % 200 == 0

    game_over = False
    state = env.reset()
    state = reduce_state(state)[RAM_mask].data.tobytes()  # Select useful bytes
    action = ql_agent.act(state)
    
    score = 0
    total_reward = 0

    while not game_over:
        if render:
            time.sleep(0.025)
            env.render()

        old_state = state
        ob, reward, game_over, _ = env.step(action)

        ob = reduce_state(ob)
        reward = reward_policy(reward, ob, action)

        total_reward += reward

        if reward == reward_policy.REWARD_IF_CROSS:
            score += 1

        state = ob[RAM_mask].data.tobytes()

        ql_agent.update_Q(old_state, state, action, reward)

        action = ql_agent.act(state)  # Next action

    scores.append(score)
    total_rewards.append(total_reward)

    print_result(i, scores, total_reward, score)

In [ ]:
for key in ql_agent.Q:
    print('{}:{}'.format(np.frombuffer(key, dtype=np.uint8, count=-1), ql_agent.Q[key]))

### 3.4. Q Learning Approximator

In [6]:
env, initial_state = environment.get_env()
ql_agent_app = agents.QLearningLinearApprox(gamma=GAMMA, available_actions=AVAILABLE_ACTIONS, N0=N0, weights_length=len(RAM_mask))
ql_agent_app.trainScaler(env, RAM_mask)

In [7]:
state = env.reset()
ql_agent_app.createFeature(reduce_state(state)[RAM_mask].data.tobytes(), 1)

array([0.02723756, 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 1.        , 1.        ])

In [8]:
%%time
scores = []
total_rewards = []

n_runs = 5
render = False
for i in range(n_runs):
#     render = i % 200 == 0

    game_over = False
    state = env.reset()
    state = reduce_state(state)[RAM_mask].data.tobytes()  # Select useful bytes
    action = ql_agent_app.act(state)
    
    score = 0
    total_reward = 0

    count = 0
    while not game_over:
        if render:
            time.sleep(0.025)
            env.render()

        old_state = state
        ob, reward, game_over, _ = env.step(action)

        ob = reduce_state(ob)
        reward = reward_policy(reward, ob, action)

        total_reward += reward

        if reward == reward_policy.REWARD_IF_CROSS:
            score += 1

        state = ob[RAM_mask].data.tobytes()
        print("Run ", count)
        print('State:',np.frombuffer(old_state, dtype=np.uint8, count=-1))
        ql_agent_app.update_W(old_state, state, action, reward)

        action = ql_agent_app.act(state)  # Next action
        count+=1
        print('------------------------------------\n')
    scores.append(score)
    total_rewards.append(total_reward)

    print_result(i, scores, total_reward, score)

Run  0
State: [2 0 0 0 0 0 0 0 0 0 0 0]
Alpha:1.0, Action:1, Reward:0.0 | Max_value:0.0 | Update: 0.0
Weight: [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
------------------------------------

Run  1
State: [2 0 0 0 0 0 0 0 0 0 0 0]
Alpha:1.0, Action:0, Reward:-0.1 | Max_value:0.0 | Update: -0.1
Weight: [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
------------------------------------

Run  2
State: [2 0 0 0 0 0 0 0 0 0 0 0]
Alpha:0.5, Action:1, Reward:0.0 | Max_value:-0.10011128267950559 | Update: 0.00048200930014660054
Weight: [-0.00272376  0.          0.          0.          0.          0.
  0.          0.          0.          0.          0.          0.
  0.         -0.1       ]
------------------------------------

Run  3
State: [3 0 0 0 0 0 0 0 0 0 0 0]
Alpha:1.0, Action:0, Reward:-0.1 | Max_value:-0.0991467276863477 | Update: -0.09852652342298991
Weight: [-0.00271063  0.          0.          0.          0.          0.
  0.          0.          0.          0.          0.          0.


Run  60
State: [30  0 12 15 20  0  0  0 23  0  0  0]
Alpha:1.0, Action:1, Reward:0.0 | Max_value:-0.2169591612125239 | Update: -0.005621998714471027
Weight: [ 0.06182049  0.          0.05328884  0.06058784  0.0856496   0.06420442
 -0.08261476 -0.00353505  0.05596273  0.          0.          0.
  0.14817967 -0.44409856]
------------------------------------

Run  61
State: [31  0 12 15 20  0  7  0 22  0  0  0]
Alpha:1.0, Action:1, Reward:0.0 | Max_value:-0.2307982302711704 | Update: 0.001993523487297727
Weight: [ 0.05952355  0.          0.05237937  0.05944978  0.08412819  0.06420442
 -0.08261476 -0.00353505  0.05421171  0.          0.          0.
  0.14255767 -0.44972056]
------------------------------------

Run  62
State: [32  0 12 15 20  0  8  0 22  0  0  0]
Alpha:1.0, Action:1, Reward:0.0 | Max_value:-0.22586385265949055 | Update: 0.002361692607836141
Weight: [ 0.06036518  0.          0.05270186  0.05985333  0.08466767  0.06420442
 -0.08242472 -0.00353505  0.05480561  0.          0. 

  0.05761422 -0.59216749]
------------------------------------

Run  120
State: [34  0 24  0  0  7 15  0  0 12 22  0]
Alpha:1.0, Action:1, Reward:0.0 | Max_value:-0.6435243098556603 | Update: 0.007275025803203827
Weight: [-0.0063686   0.01253153 -0.02750736  0.0736987   0.17062487  0.0620671
 -0.0620775  -0.08222912  0.1036184  -0.15497885 -0.10086852  0.
  0.05761422 -0.62818336]
------------------------------------

Run  121
State: [34  0 24  0  0  8 15  0  0 12 22  0]
Alpha:1.0, Action:1, Reward:0.0 | Max_value:-0.6262640494304585 | Update: 0.00543747127916161
Weight: [-0.00299998  0.01253153 -0.02515359  0.0736987   0.17062487  0.06275613
 -0.06059137 -0.08222912  0.1036184  -0.1538     -0.09870258  0.
  0.06488924 -0.62090834]
------------------------------------

Run  122
State: [34  0 24  0  0  8 16  0  0 12 22  0]
Alpha:1.0, Action:1, Reward:0.0 | Max_value:-0.6109270532513673 | Update: 0.007905835369191427
Weight: [-4.82223775e-04  1.25315298e-02 -2.33943484e-02  7.36986963e-0

Run  178
State: [48  0  0  0  7  0 21  0 15  0  7 16]
Alpha:1.0, Action:0, Reward:-0.1 | Max_value:-0.9811798609890893 | Update: 0.04097272207183811
Weight: [-0.21280351  0.01172914 -0.00994827  0.0736987   0.17854312 -0.00668334
 -0.00718992 -0.13222193 -0.0021484  -0.14135727 -0.15814389 -0.10816103
  0.13125884 -0.94939414]
------------------------------------

Run  179
State: [48  0  0  0  7  0 22  0 15  0  7 16]
Alpha:1.0, Action:1, Reward:0.0 | Max_value:-0.9149517396538827 | Update: 0.009062561445610795
Weight: [-0.18601958  0.01172914 -0.00994827  0.0736987   0.18242389 -0.00668334
  0.00452789 -0.13222193  0.00617422 -0.14135727 -0.15426254 -0.09934457
  0.13125884 -0.90842142]
------------------------------------

Run  180
State: [49  0  0  0  8  0 23  0 14  0  7 16]
Alpha:1.0, Action:1, Reward:0.0 | Max_value:-0.8934339779184367 | Update: 0.0065803017557013455
Weight: [-0.18009537  0.01172914 -0.00994827  0.0736987   0.18328226 -0.00668334
  0.00724311 -0.13222193  0.0080150


Run  241
State: [ 2  0  0  7  0 14  0 23  0 25  0  0]
Alpha:1.0, Action:0, Reward:-0.1 | Max_value:138.27696546366246 | Update: -1.2024227646352585
Weight: [ 4.24225091e+01  1.09983998e-02 -9.94826990e-03 -4.00454029e+00
  4.96524210e+01  2.07200238e+01  4.29073509e+01 -1.69677085e+01
 -1.12243916e-02 -1.77536338e+01 -1.46208355e-01  1.01732406e-01
 -6.85081908e-01  1.44551219e+02]
------------------------------------

Run  242
State: [ 2  0  0  7  0 15  0 23  0 25  0  0]
Alpha:1.0, Action:1, Reward:0.0 | Max_value:136.99783416799164 | Update: -0.4510262482899918
Weight: [ 4.23897581e+01  1.09983998e-02 -9.94826990e-03 -4.11813002e+00
  4.96524210e+01  2.04922569e+01  4.29073509e+01 -1.73406952e+01
 -1.12243916e-02 -1.81595516e+01 -1.46208355e-01  1.01732406e-01
 -6.85081908e-01  1.43348796e+02]
------------------------------------

Run  243
State: [ 2  0  0  7  0 15  0 22  0 25  0  0]
Alpha:1.0, Action:1, Reward:0.0 | Max_value:137.13386239178757 | Update: 0.4676730612151516
Weight: 

...

State: [ 9  0 11  0 18  0  0  0  0  0 26  0]
Alpha:0.5, Action:0, Reward:-0.1 | Max_value:222109.19518007763 | Update: -1110.595975900389
Weight: [ 16629.81607705  -1387.79821565  93848.29532616 -56087.26474783
 -55189.67952927 137580.09580899 -13198.09953726  47476.42589571
  21397.10184102  82890.00352493   3069.53906893  -1227.9128101
  -1721.6469557  218515.87662917]
------------------------------------

Run  2436
State: [ 9  0 11  0 18  0  0  0  0  0 26  0]
Alpha:0.3333333333333333, Action:0, Reward:-0.1 | Max_value:220754.11965259074 | Update: -735.8803988419725
Weight: [ 16493.69142995  -1387.79821565  93683.60552165 -56087.26474783
 -55460.17100945 137580.09580899 -13198.09953726  47476.42589571
  21397.10184102  82890.00352493   2678.77096113  -1227.9128101
  -1721.6469557  217405.28065327]
------------------------------------

Run  2437
State: [ 9  0 11  0 18  0  0  0  0  0 26  0]
Alpha:0.25, Action:0, Reward:-0.1 | Max_value:219070.6515388828 | Update: -744.100547073358
Weig

Run  2494
State: [16  0 23  0  0  0  7  0 22 15 11  0]
Alpha:1.0, Action:0, Reward:-0.1 | Max_value:285362.14236241305 | Update: -3865.9911591811106
Weight: [ 21501.4703949   -1387.79821565  94355.38127344 -56087.26474783
 -39554.25143241 121009.40991824   5415.55665406  51259.01161744
  19969.7093357   80426.2431893    7436.15029042  -1227.9128101
  -1778.56541138 228570.51392161]
------------------------------------

Run  2495
State: [16  0 23  0  0  0  8  0 22 14 11  0]
Alpha:1.0, Action:0, Reward:-0.1 | Max_value:280045.0047860667 | Update: -3079.488765228074
Weight: [ 20659.0691478   -1387.79821565  93156.69198104 -56087.26474783
 -39554.25143241 121009.40991824   5047.01112167  51259.01161744
  18817.96127263  79643.18694733   6860.65309685  -1227.9128101
  -1778.56541138 224704.52276243]
------------------------------------

Run  2496
State: [16  0 23  0  0  0  9  0 21 14 10  0]
Alpha:1.0, Action:0, Reward:-0.1 | Max_value:276113.29817163385 | Update: -2697.0689150989638
Weight:


Run  2557
State: [38  0  0  0  0  9 17  0  0  0  0 17]
Alpha:1.0, Action:0, Reward:-0.1 | Max_value:149913.07148236412 | Update: -1510.975010515016
Weight: [-6.36477510e+03 -1.38779822e+03  7.84413150e+04 -5.60872647e+04
 -3.95542514e+04  1.21009518e+05 -5.20991052e+03  4.29619538e+04
  5.73489051e+03  7.15550442e+04  2.23907635e+03 -1.90111947e+04
  5.92073574e+01  1.44035743e+05]
------------------------------------

Run  2558
State: [38  0  0  0  0  9 18  0  0  0  0 17]
Alpha:1.0, Action:1, Reward:0.0 | Max_value:145985.11214273365 | Update: -3285.0289774685807
Weight: [-7.14672520e+03 -1.38779822e+03  7.84413150e+04 -5.60872647e+04
 -3.95542514e+04  1.20825523e+05 -5.55972554e+03  4.29619538e+04
  5.73489051e+03  7.15550442e+04  2.23907635e+03 -1.93566450e+04
  5.92073574e+01  1.42524768e+05]
------------------------------------

Run  2559
State: [39  0  0  0  6 10 20  0  0  0  0 17]
Alpha:1.0, Action:1, Reward:0.0 | Max_value:140550.38998846407 | Update: 1077.9506052098295
Weight


Run  2614
State: [ 5  0  0 18 24  0 18  0 17  0  0  6]
Alpha:1.0, Action:1, Reward:0.0 | Max_value:131363.25102800215 | Update: -1481.8034751114756
Weight: [-4.55016931e+03 -1.38779822e+03  7.84413150e+04 -5.24184975e+04
 -3.48554418e+04  1.15994968e+05  1.47263442e+02  3.82616412e+04
  7.99076530e+03  7.15550442e+04  2.23907635e+03 -1.84780115e+04
  6.10575776e+02  1.54898332e+05]
------------------------------------

Run  2615
State: [ 6  0  0 18 24  0 19  0 16  0  0  6]
Alpha:1.0, Action:0, Reward:-0.1 | Max_value:130339.10932042956 | Update: 194.24447055776545
Weight: [ -4651.07107324  -1387.79821565  78441.31495162 -52778.45143022
 -35336.64313758 115994.96825884   -215.97798106  38261.64120886
   7649.64035412  71555.04417956   2239.07635419 -18597.58128012
   -871.22769935 153416.52856622]
------------------------------------

Run  2616
State: [ 6  0  0 18 24  0 20  0 16  0  0  0]
Alpha:0.5, Action:0, Reward:-0.1 | Max_value:130005.70837072353 | Update: -941.9271788653641
Weigh

Run  2673
State: [19  0  0  0  0 11 22  0  0 10 21  0]
Alpha:0.5, Action:1, Reward:0.0 | Max_value:238439.21406742808 | Update: -1199.3967227506218
Weight: [-5.17818859e+03 -1.43333362e+03  7.84413150e+04 -3.59729189e+04
 -1.02320499e+04  1.15309076e+05  2.33724175e+04  5.64540493e+04
  2.36373314e+04  8.20238742e+04 -1.95114787e+02 -1.85819073e+04
 -7.72254119e+02  2.05380915e+05]
------------------------------------

Run  2674
State: [19  0  0  0  0 11 23  0  0  9 20  0]
Alpha:1.0, Action:0, Reward:-0.1 | Max_value:238779.59686608883 | Update: -516.7461893930158
Weight: [ -5488.54063891  -1433.33362212  78441.31495162 -35972.91893406
 -10232.04985166 115130.5668856   23013.06738148  56454.04928355
  23637.33143616  81861.91569952   -535.97147625 -18581.90729641
  -1971.65084136 204181.51874873]
------------------------------------

Run  2675
State: [19  0  0  0  0 12 24  0  0  9 20  0]
Alpha:1.0, Action:0, Reward:-0.1 | Max_value:238428.5765015686 | Update: -2073.1844515080156
Weight

In [ ]:
print_result(i, scores, total_reward, score)

In [ ]:
scores

In [ ]:
ql_agent_app.update_W(old_state, state, action, reward)

In [ ]:
old_state, state, action, reward

In [ ]:
teste = np.frombuffer(state, dtype=np.uint8, count=-1)
teste.reshape(1,-1)

In [ ]:
from sklearn.preprocessing import normalize

In [ ]:
normalize(teste.reshape(1,-1), norm='l1', axis=0)

In [ ]:
scaler = StandardScaler(with_mean=False)
observation_examples = np.array([env.observation_space.sample()[RAM_mask] for x in range(10000)])
scaler.fit(observation_examples)

In [ ]:
scaler.transform([[1,0,1,0,0,1,0,1,0,0,1,1]])

In [ ]:
np.append([1,2,3],[1,2])